In [3]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [1]:
import pandas as pd
import requests
import numpy as np
import time
from collections import Counter

from datetime import datetime, timedelta
import matplotlib.pyplot as plt

from PIL import Image
from scipy.stats import gaussian_kde

import warnings

# FutureWarning 무시 설정
warnings.filterwarnings("ignore", category=FutureWarning)
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)


# PUGB API KEY

In [ ]:
# PUBG API URL 및 API KEY 설정
API_URL = "https://api.pubg.com"
# API_KEY = 'eyJ0eXAiOiJKV1QiLCJhbGciOiJIUzI1NiJ9

In [ ]:
# 요청 헤더 설정
headers = {
    "Authorization": f"Bearer {API_KEY}",
    "Accept": "application/vnd.api+json"
}

# player id 별 matchid
def get_player_id(player_name):
    endpoint = f"/shards/steam/players?filter[playerNames]={player_name}"
    response = requests.get(API_URL + endpoint, headers=headers)
    if response.status_code == 200:
        data = response.json()
        if data:
            return data['data'][0]['relationships']['matches']['data']
        else:
            print(f"플레이어 {player_name}을 찾을 수 없습니다.")
            return None
    elif response.status_code == 429:
        print("API 요청이 너무 많습니다. 1분 동안 쉽니다.")
        time.sleep(60)  # 1분 동안 코드 실행을 지연시킵니다.
        return get_player_id(player_name)  # 재귀적으로 다시 시도합니다.
    else:
        print(f"Error: {response.status_code}")
        return None



# # matchid 별 경기
# def get_match_details(match_id):
#     url = 'https://api.pubg.com/shards/steam/matches/{}'
#     url = url.format(match_id)
#     response = requests.get(url, headers=headers)

#     if response.status_code == 200:
#         return response.json()
#     else:
#         print(f"Error: {response.status_code}")
#         return None


# matchid 별로 경기 요약
# def get_match_details(match_ids):
#     all_match_details = []

#     for match_id in match_ids:
#         url = f'https://api.pubg.com/shards/steam/matches/{match_id}'
#         response = requests.get(url, headers=headers)

#         if response.status_code == 200:
#             all_match_details.append(response.json())

#         else:
#             print(f"Error: {response.status_code} for match ID {match_id}")

#     return all_match_details


# matchid 별로 경기 요약
def get_match_details(match_ids):
    all_match_details = []

    for i, match_id in enumerate(match_ids):
        url = f'https://api.pubg.com/shards/steam/matches/{match_id}'
        response = requests.get(url, headers=headers)

        if response.status_code == 200:
            all_match_details.append(response.json())
        else:
            print(f"Error: {response.status_code} for match ID {match_id}")

        # 10개마다 1분 대기
        if (i + 1) % 10 == 0:
            print("Reached 10 requests, waiting for 1 minute...")
            time.sleep(61)

    return all_match_details



👉🏻 특정 기간동안의 매치데이터의 경우 sample 데이터만 수집이 가능하다..그런데 실제 유저의 데이터가 아니라 전부 ai 대결임

In [ ]:

def sample_player_data():
  # PUBG API endpoint and headers
  api_url = "https://api.pubg.com/shards/steam/matches"

  # Format the times in ISO 8601 format
  end_time_str = '2024-06-03T00:00:00Z' #end_time.strftime("%Y-%m-%dT%H:%M:%SZ")
  start_time_str = '2024-05-30T00:00:00Z' #start_time.strftime("%Y-%m-%dT%H:%M:%SZ")

  # Construct the URL with the query parameters
  params = {
      "filter[createdAt-start]": start_time_str,
      "filter[createdAt-end]": end_time_str
  }

  # Make the API request
  response = requests.get(api_url, headers=headers, params=params)
  data = response.json()
  return data


* 특정 유저별 최근 matchid 가져오기

In [ ]:
player_name = 'VINGMINGVINGMING' # xiaosusu-9527 # 5b3f0f4b-7f8b-4d61-88a6-715a7186b7fa
data = get_player_id(player_name)
match_ids = [match['id'] for match in data]


In [ ]:
ids = match_ids[:20]

* includid 매치별 참가자 기본통계
* 전투로그 같은 세부 정보는 asset key 를 이용해서 수집해야함

In [ ]:
match_datas = get_match_details(match_ids)

Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10

In [ ]:
len(match_datas)

1020

### 매치 기본 통계와 Detail Log

In [ ]:
match_datas[0]['data']['id'] # matchid
# match_datas[0]['data']['attributes']['gameMode'] # game mode (Duo, Solo ...)
# match_datas[0]['data']['attributes']['mapName'] # 맵 이름

'af3e06f5-d61b-4eac-b914-97c27bc23cda'

* 여러명의 player, matchids

In [ ]:
log_details = []
all_match_static = []
for i in range(len(match_ids)):
    match_data = match_datas[i]

    if match_data is None:
        continue  # match_datas[i]가 None인 경우 건너뜁니다.

    match_static = pd.json_normalize(match_data['included'], sep='_')
    all_match_static.append(match_static)

    # GameMode와 MapName 정보를 가져와서 DataFrame에 추가합니다.
    matchId = match_data['data']['id']
    game_mode = match_data['data']['attributes']['gameMode']
    map_name = match_data['data']['attributes']['mapName']

    # match_static DataFrame에 새로운 컬럼을 추가합니다.
    match_static['GameMode'] = game_mode
    match_static['MapName'] = map_name
    match_static['matchId'] = matchId


    # 각 asset의 URL과 관련 정보를 함께 저장합니다.
    asset_urls = match_static[match_static['type'] == 'asset']['attributes_URL'].tolist()
    for url in asset_urls:
        log_details.append({
            'url': url,
            'game_mode': game_mode,
            'map_name': map_name,
            'matchId': matchId
        })



result = pd.concat(all_match_static, ignore_index=True)
result.columns = result.columns.str.replace('attributes_stats_', '')


In [ ]:
player_names = result['name'].dropna().tolist()

In [ ]:
test_player = player_names[:20]

In [ ]:
# 플레이어 리스트에서 모든 match IDs를 가져오는 함수
def get_all_match_ids(player_names):
    all_match_ids = []
    for player_name in player_names:
        match_ids = get_player_id(player_name)
        if match_ids:
            all_match_ids.extend([match['id'] for match in match_ids])
    return all_match_ids

all_match_ids = get_all_match_ids(test_player)

len(all_match_ids)

API 요청이 너무 많습니다. 1분 동안 쉽니다.


1077

In [ ]:
#  중복없는 match_id 저장
match_ids = set(all_match_ids)
file_name = './test.txt'
with open(file_name, 'w+') as file:
    file.write('\n'.join(match_ids))

In [ ]:
# matchid 불러오기
file_name = '/content/test.txt'
# 파일을 읽어서 리스트로 저장
with open(file_name, 'r') as file:
    match_ids = file.read().splitlines()


In [ ]:
# match_datas 저장
csv_file_path = '/content/match_datas.csv'
result.to_csv(csv_file_path, index=False)


In [ ]:
len(result)

133681

* URL을 통해 불러오는 세부 데이터에는 MAP,DUO,MATCHID 정보가 없으므로 따로 추가해야하는 과정이 필요하다.

In [ ]:
log_details

[{'url': 'https://telemetry-cdn.pubg.com/bluehole-pubg/steam/2024/06/01/14/22/653359f9-2022-11ef-8a2b-5e46f6070314-telemetry.json',
  'game_mode': 'squad',
  'map_name': 'Savage_Main',
  'matchId': '612d59c5-2f5b-4f0e-81ae-55938494ba00'},
 {'url': 'https://telemetry-cdn.pubg.com/bluehole-pubg/steam/2024/05/24/14/31/5fe5ffdb-19da-11ef-80cd-1a86b955c47e-telemetry.json',
  'game_mode': 'duo',
  'map_name': 'Savage_Main',
  'matchId': 'cfdfb256-c8a3-4433-8497-ca044c538569'},
 {'url': 'https://telemetry-cdn.pubg.com/bluehole-pubg/steam/2024/05/25/17/47/ce4ecb79-1abe-11ef-81c6-b61ecf1a0c3f-telemetry.json',
  'game_mode': 'duo',
  'map_name': 'Chimera_Main',
  'matchId': 'db90f577-5b44-4e15-83f8-1fd0339ce73f'},
 {'url': 'https://telemetry-cdn.pubg.com/bluehole-pubg/steam/2024/05/30/12/40/dba1385d-1e81-11ef-ac0d-96c5c9cfbdb7-telemetry.json',
  'game_mode': 'duo',
  'map_name': 'DihorOtok_Main',
  'matchId': 'ec083b0c-6720-4cf8-a233-8f61bae8caf3'},
 {'url': 'https://telemetry-cdn.pubg.com/blueh

In [ ]:
# log_details를 줄바꿈으로 구분하여 문자열로 변환
log_details_str = '\n'.join(map(str, log_details))

# 저장
file_name = 'log_details.txt'
with open(file_name, 'w') as file:
    file.write(log_details_str)


In [ ]:
# 게임타입 스쿼드가 제일 많음
solo_log = [log for log in log_details if log['game_mode'] == 'solo']
duo_log = [log for log in log_details if log['game_mode'] == 'duo']
squad_log = [log for log in log_details if log['game_mode'] == 'squad']

len(solo_log)

45

In [ ]:
# 각 URL에 대해 요청을 보내고 응답 데이터를 DataFrame으로 변환하고 필요한 컬럼을 추가합니다.

def get_details(log_details):
  all_logs = []
  for i, detail in enumerate(log_details):
      url = detail['url']
      response = requests.get(url, headers=headers)
      if response.status_code == 200:
          logs = response.json()
          df = pd.json_normalize(logs)
          df['GameMode'] = detail['game_mode']
          df['MapName'] = detail['map_name']
          df['matchId'] = detail['matchId']
          all_logs.append(df)
      else:
          print(f"Failed to fetch data from {url}: {response.status_code}")

      # 10개마다 1분 대기
      if (i + 1) % 10 == 0:
          print("Reached 10 requests, waiting for 1 minute...")
          time.sleep(61)

  # 모든 로그 DataFrame을 결합합니다.
  all_logs_df = pd.concat(all_logs, ignore_index=True)

  return all_logs_df

all_logs_df = get_details(solo_log)


Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...
Reached 10 requests, waiting for 1 minute...


In [ ]:
len(all_logs_df)

1100190

In [ ]:
# match_datas 저장
csv_file_path = '/content/drive/MyDrive/solo_log_data.csv'
all_logs_df.to_csv(csv_file_path, index=False)

# 주제 : 총기 밸런스

총기 밸런스 패치를 하기위해 어떤 정보를 봐야할까? 그리고 어떻게 전처리해야할까


라운드별 총기 인기도, 총기 상성(예를 들어 밴달 사용자와 팬텀 사용자의 맞대결에서 누가 우위에 있는지)


## 조건

* 다른 사람 개입 없이 1:1 싸움인 경우 (혹은 제3자 개입이 있는 경우 같이)
* 미러전은 따로 봐야함 (스카 vs 스카)
* 일방적인 공격이 아니어야함 (전면전 이어야함)
* 거리별로 다르게 봐야함
* 파츠별로 다르게 봐야함
* 도중 회복한 경우 어떻게 봐야할까..?

## 분석지표 정리

* 정확도, 탄퍼짐, 반동회복, 발사한 탄환수, 적중한 탄환

발로란트에서는 5초 이내에 발생한 멀티킬을 총기의 난사 제어를 알아보는데 지표로 사용

* 부위별 적중도
* 거리별 적중도 (5m 단위?)
* 총기 인기도
* 총기별 게임승률
* 1:1 전면전 승률
*

# 29.1 패치노트

SCAR-L과 AKM의 경우, 낮은 사용성과 승률로 인해 상향이 필요하다는 의견
* AKM : 피해량을 소폭 증가 (다른 AR에 비해 피해량이 강화)
* SCAR-L : 낮은 연사 속도를 소폭 증가 + 수직/수평 반동 각 4%씩 감소

* 판처파우스트에 장착 모션을 추가. 빠르게 줍거나 교체하여 발사할 수 없도록 조정

* Mk12의 경우 현재 가장 범용적으로 사용되는 DMR 총기 -> 사운드 인지 어려움(소음기+라이트그립 장착시 OP) -> 사운드만 조정


## 패치에 따른 사용성 분석
👉🏻 SCAR-L 과 AKM 의 사용성 체크 \

## 이외에 총기 분석 주제
> 근접전에서 가장 유리한 총은?
* 거리별 kill 지표




In [ ]:

# row 생략 없이 출력
pd.set_option('display.max_rows', None)
# col 생략 없이 출력
pd.set_option('display.max_columns', None)


cols= pd.DataFrame(df.columns)
cols

0
0                                            accountId
1                                                   _D
2                                                   _T
3                                        common.isGame
4                                       character.name
5                                     character.teamId
6                                     character.health
7                                 character.location.x
8                                 character.location.y
9                                 character.location.z
10                                   character.ranking
11                         character.individualRanking
12                                 character.accountId
13                              character.isInBlueZone
14                               character.isInRedZone
15                                      character.zone
16                                      character.type
17                                         item.itemId
18                                     item.stackCount
19                                       item.category
20                                    item.subCategory
21                                  item.attachedItems
22                                             vehicle
23                                         elapsedTime
24                                     numAlivePlayers
25                                            attackId
26                                fireWeaponStackCount
27                                          attackType
28                                       attacker.name
29                                     attacker.teamId
30                                     attacker.health
31                                 attacker.location.x
32                                 attacker.location.y
33                                 attacker.location.z
34                                    attacker.ranking
35                          attacker.individualRanking
36                                  attacker.accountId
37                               attacker.isInBlueZone
38                                attacker.isInRedZone
39                                       attacker.zone
40                                       attacker.type
41                                       weapon.itemId
42                                   weapon.stackCount
43                                     weapon.category
44                                  weapon.subCategory
45                                weapon.attachedItems
46                                         isLedgeGrab
47                                          objectType
48                                    objectTypeStatus
49                            objectTypeAdditionalInfo
50                                            weaponId
51                                           fireCount
52                                           seatIndex
53                                    fellowPassengers
54                                 vehicle.vehicleType
55                                   vehicle.vehicleId
56                                   vehicle.seatIndex
57                               vehicle.healthPercent
58                                 vehicle.feulPercent
59                                 vehicle.altitudeAbs
60                                 vehicle.altitudeRel
61                                    vehicle.velocity
62                               vehicle.isWheelsInAir
63                             vehicle.isInWaterVolume
64                                  vehicle.isEngineOn
65                                             mapName
66                                           weatherId
67                                          characters
68                                 cameraViewBehaviour
69                                            teamSize
70                                        isCustomGame
71                                         isEventMode
72                               blueZ

In [ ]:
df[['_T']].value_counts()

# LogPlayerPosition
# LogHeal

_T                          
LogPlayerPosition               5624
LogPlayerTakeDamage             4092
LogPlayerAttack                 3742
LogItemPickup                   3408
LogHeal                         2515
LogItemEquip                    1620
LogItemUnequip                  1405
LogItemAttach                    922
LogItemDetach                    909
LogItemUse                       896
LogItemDrop                      700
LogVaultStart                    629
LogObjectInteraction             620
LogItemPickupFromLootBox         344
LogPlayerUseThrowable            288
LogWeaponFireCount               282
LogVehicleRide                   149
LogVehicleLeave                  149
LogGameStatePeriodic             137
LogParachuteLanding              111
LogPlayerCreate                  101
LogPlayerLogin                    99
LogPlayerLogout                   99
LogPlayerKillV2                   94
LogPlayerMakeGroggy               59
LogVehicleDamage                  44
LogItemPi

In [ ]:
import re
kill_df = df[df['_T'].isin(['LogPlayerPosition','LogPlayerKillV2','LogPlayerAttack','LogPlayerTakeDamage','LogPlayerPosition','LogHeal'])] # 'LogPlayerKillV2','LogPlayerAttack',
# kill_df = kill_df.filter(regex=re.compile('_D|_T|attack|victim')) # |dBNO|wepon|finish
kill_df[(kill_df['attacker.name']== player_name)] #| (kill_df['victim.name'] == player_name)].sort_values(by=['_D']) #| (kill_df['dBNOMaker.name'] == player_name) | (kill_df['finisher.name'] == player_name)].sort_values(by=['_D'])


In [ ]:
kill_df[kill_df['_T'] == 'LogPlayerPosition'].sample(100)

MatchId PingQuality                        _D                 _T  \
28063     NaN         NaN  2024-05-24T14:23:17.658Z  LogPlayerPosition   
28577     NaN         NaN  2024-05-24T14:24:07.382Z  LogPlayerPosition   
30117     NaN         NaN  2024-05-24T14:26:02.445Z  LogPlayerPosition   
13161     NaN         NaN  2024-05-24T14:13:45.748Z  LogPlayerPosition   
5063      NaN         NaN  2024-05-24T14:11:23.073Z  LogPlayerPosition   
20333     NaN         NaN  2024-05-24T14:17:30.933Z  LogPlayerPosition   
15196     NaN         NaN  2024-05-24T14:14:31.643Z  LogPlayerPosition   
16836     NaN         NaN  2024-05-24T14:15:14.295Z  LogPlayerPosition   
25040     NaN         NaN  2024-05-24T14:20:50.487Z  LogPlayerPosition   
26688     NaN         NaN  2024-05-24T14:21:50.528Z  LogPlayerPosition   
6423      NaN         NaN  2024-05-24T14:11:39.295Z  LogPlayerPosition   
14352     NaN         NaN  2024-05-24T14:14:10.628Z  LogPlayerPosition   
21857     NaN         NaN  2024-05-24T14:18:50.179Z  LogPlayerPosition   
3858      NaN         NaN  2024-05-24T14:10:42.231Z  LogPlayerPosition   
3319      NaN         NaN  2024-05-24T14:09:55.741Z  LogPlayerPosition   
27716     NaN         NaN  2024-05-24T14:22:48.432Z  LogPlayerPosition   
4599      NaN         NaN  2024-05-24T14:11:13.087Z  LogPlayerPosition   
4489      NaN         NaN  2024-05-24T14:11:10.646Z  LogPlayerPosition   
4121      NaN         NaN  2024-05-24T14:10:59.170Z  LogPlayerPosition   
33761     NaN         NaN  2024-05-24T14:31:31.625Z  LogPlayerPosition   
32282     NaN         NaN  2024-05-24T14:28:54.647Z  LogPlayerPosition   
8859      NaN         NaN  2024-05-24T14:12:20.961Z  LogPlayerPosition   
9428      NaN         NaN  2024-05-24T14:12:30.616Z  LogPlayerPosition   
29630     NaN         NaN  2024-05-24T14:25:38.189Z  LogPlayerPosition   
22773     NaN         NaN  2024-05-24T14:19:24.644Z  LogPlayerPosition   
9572      NaN         NaN  2024-05-24T14:12:33.021Z  LogPlayerPosition   
4279      NaN         NaN  2024-05-24T14:11:04.405Z  LogPlayerPosition   
2288      NaN         NaN  2024-05-24T14:09:48.165Z  LogPlayerPosition   
24720     NaN         NaN  2024-05-24T14:20:38.588Z  LogPlayerPosition   
23890     NaN         NaN  2024-05-24T14:20:08.050Z  LogPlayerPosition   
29123     NaN         NaN  2024-05-24T14:25:01.610Z  LogPlayerPosition   
33067     NaN         NaN  2024-05-24T14:30:16.480Z  LogPlayerPosition   
9870      NaN         NaN  2024-05-24T14:12:38.049Z  LogPlayerPosition   
19869     NaN         NaN  2024-05-24T14:17:08.151Z  LogPlayerPosition   
4859      NaN         NaN  2024-05-24T14:11:19.272Z  LogPlayerPosition   
4328      NaN         NaN  2024-05-24T14:11:05.831Z  LogPlayerPosition   
8656      NaN         NaN  2024-05-24T14:12:17.607Z  LogPlayerPosition   
31844     NaN         NaN  2024-05-24T14:27:47.238Z  LogPlayerPosition   
34685     NaN         NaN  2024-05-24T14:32:48.168Z  LogPlayerPosition   
31618     NaN         NaN  2024-05-24T14:27:30.204Z  LogPlayerPosition   
909       NaN         NaN  2024-05-24T14:09:24.393Z  LogPlayerPosition   
13084     NaN         NaN  2024-05-24T14:13:44.767Z  LogPlayerPosition   
3930      NaN         NaN  2024-05-24T14:10:47.617Z  LogPlayerPosition   
6744      NaN         NaN  2024-05-24T14:11:44.775Z  LogPlayerPosition   
4303      NaN         NaN  2024-05-24T14:11:05.271Z  LogPlayerPosition   
25967     NaN         NaN  2024-05-24T14:21:21.634Z  LogPlayerPosition   
19499     NaN         NaN  2024-05-24T14:16:52.442Z  LogPlayerPosition   
13658     NaN         NaN  2024-05-24T14:13:55.429Z  LogPlayerPosition   
28281     NaN         NaN  2024-05-24T14:23:37.233Z  LogPlayerPosition   
24589     NaN         NaN  2024-05-24T14:20:33.076Z  LogPlayerPosition   
932       NaN         NaN  2024-05-24T14:09:24.966Z  LogPlayerPosition   
29947     NaN         NaN  2024-05-24T14:25:52.458Z  LogPlayerPosition   
10327     NaN         NaN  2024-05-24T14:12:47.708Z  LogPlayerPosition   
4297      

In [ ]:
# 힐을 사용한 유저의 컬럼은 character.name 에서 남음.
heal_df = df[df['_T'].isin(['LogPlayerTakeDamage'])]
heal_df.head(100)

MatchId PingQuality                        _D                   _T  \
4071     NaN         NaN  2024-05-24T14:10:56.564Z  LogPlayerTakeDamage   
4110     NaN         NaN  2024-05-24T14:10:58.582Z  LogPlayerTakeDamage   
4150     NaN         NaN  2024-05-24T14:10:59.874Z  LogPlayerTakeDamage   
4152     NaN         NaN  2024-05-24T14:10:59.909Z  LogPlayerTakeDamage   
4180     NaN         NaN  2024-05-24T14:11:00.701Z  LogPlayerTakeDamage   
4184     NaN         NaN  2024-05-24T14:11:00.782Z  LogPlayerTakeDamage   
4192     NaN         NaN  2024-05-24T14:11:00.883Z  LogPlayerTakeDamage   
4203     NaN         NaN  2024-05-24T14:11:01.122Z  LogPlayerTakeDamage   
4224     NaN         NaN  2024-05-24T14:11:02.264Z  LogPlayerTakeDamage   
4239     NaN         NaN  2024-05-24T14:11:02.615Z  LogPlayerTakeDamage   
4243     NaN         NaN  2024-05-24T14:11:02.797Z  LogPlayerTakeDamage   
4261     NaN         NaN  2024-05-24T14:11:03.810Z  LogPlayerTakeDamage   
4277     NaN         NaN  2024-05-24T14:11:04.296Z  LogPlayerTakeDamage   
4292     NaN         NaN  2024-05-24T14:11:04.805Z  LogPlayerTakeDamage   
4305     NaN         NaN  2024-05-24T14:11:05.304Z  LogPlayerTakeDamage   
4327     NaN         NaN  2024-05-24T14:11:05.830Z  LogPlayerTakeDamage   
4339     NaN         NaN  2024-05-24T14:11:06.301Z  LogPlayerTakeDamage   
4351     NaN         NaN  2024-05-24T14:11:06.807Z  LogPlayerTakeDamage   
4364     NaN         NaN  2024-05-24T14:11:07.309Z  LogPlayerTakeDamage   
4387     NaN         NaN  2024-05-24T14:11:07.814Z  LogPlayerTakeDamage   
4400     NaN         NaN  2024-05-24T14:11:08.289Z  LogPlayerTakeDamage   
4424     NaN         NaN  2024-05-24T14:11:08.837Z  LogPlayerTakeDamage   
4437     NaN         NaN  2024-05-24T14:11:09.297Z  LogPlayerTakeDamage   
4449     NaN         NaN  2024-05-24T14:11:09.796Z  LogPlayerTakeDamage   
4476     NaN         NaN  2024-05-24T14:11:10.309Z  LogPlayerTakeDamage   
4500     NaN         NaN  2024-05-24T14:11:10.794Z  LogPlayerTakeDamage   
4522     NaN         NaN  2024-05-24T14:11:11.311Z  LogPlayerTakeDamage   
4538     NaN         NaN  2024-05-24T14:11:11.824Z  LogPlayerTakeDamage   
4557     NaN         NaN  2024-05-24T14:11:12.281Z  LogPlayerTakeDamage   
4583     NaN         NaN  2024-05-24T14:11:12.826Z  LogPlayerTakeDamage   
4615     NaN         NaN  2024-05-24T14:11:13.315Z  LogPlayerTakeDamage   
4642     NaN         NaN  2024-05-24T14:11:13.809Z  LogPlayerTakeDamage   
4666     NaN         NaN  2024-05-24T14:11:14.308Z  LogPlayerTakeDamage   
4700     NaN         NaN  2024-05-24T14:11:14.811Z  LogPlayerTakeDamage   
4715     NaN         NaN  2024-05-24T14:11:15.288Z  LogPlayerTakeDamage   
4731     NaN         NaN  2024-05-24T14:11:15.801Z  LogPlayerTakeDamage   
4747     NaN         NaN  2024-05-24T14:11:16.304Z  LogPlayerTakeDamage   
4762     NaN         NaN  2024-05-24T14:11:16.828Z  LogPlayerTakeDamage   
4782     NaN         NaN  2024-05-24T14:11:17.290Z  LogPlayerTakeDamage   
4802     NaN         NaN  2024-05-24T14:11:17.797Z  LogPlayerTakeDamage   
4822     NaN         NaN  2024-05-24T14:11:18.283Z  LogPlayerTakeDamage   
4846     NaN         NaN  2024-05-24T14:11:18.814Z  LogPlayerTakeDamage   
4860     NaN         NaN  2024-05-24T14:11:19.307Z  LogPlayerTakeDamage   
4882     NaN         NaN  2024-05-24T14:11:19.813Z  LogPlayerTakeDamage   
4905     NaN         NaN  2024-05-24T14:11:20.279Z  LogPlayerTakeDamage   
4907     NaN         NaN  2024-05-24T14:11:20.294Z  LogPlayerTakeDamage   
4940     NaN         NaN  2024-05-24T14:11:20.827Z  LogPlayerTakeDamage   
4964     NaN         NaN  2024-05-24T14:11:21.285Z  LogPlayerTakeDamage   
4992     NaN         NaN  2024-05-24T14:11:21.796Z  LogPlayerTakeDamage   
5024     NaN         NaN  2024-05-24T14:11:22.292Z  LogPlayerTakeDamage   
5048     NaN         NaN  2024-05-24T14:11:22.851Z  LogPlayerTakeDamage   
5066     NaN         NaN  2024-05-24T14:11:23.159Z  LogPlayerTakeDamage   
5080     NaN         NaN  2024

## 지표와 관련하여 규칙 정리

* LogPlayerTakeDamage 에서 attacker.name	가 없는 경우 자기장에 맞은 것
* position 은 10초 단위로 남겨지고 있음
* 사람간의 전투만 필요하므로 _T 가 LogPlayerTakeDamage 이고 attacker.name 이 nan 인경우 제거해야함
* 확정 KILL을 한 경우, 거리에 관한 지표가 나온다.
* 하지만 공격 당시의 세세한 로그는, Attack한 사람과 Damage를 받은 사람간의 좌표의 차이를 통해서 거리를 구해야한다.

* fireWeaponStackCount 은 총기별로 누적 카운트 된다.
* 총기별로 몇발을 쏘고(`fireWeaponStackCount`), 얼만큼 맞췄는지 (`LogTakeDamage`) 구할 수 있다.  


In [ ]:
# 확정킬 log
# LogPlayerKill_df = df[df['_T'] == 'LogPlayerKillV2']

LogPlayerKill_df = df[df['_T'].isin(['LogPlayerPosition','LogPlayerKillV2','LogPlayerAttack','LogPlayerTakeDamage','LogHeal'])] # 'LogPlayerKillV2','LogPlayerAttack',


kill_sample = LogPlayerKill_df[['_D','_T',
                  'character.name','character.health','healAmount','' # healLog와 관련된 컬럼
                  'attacker.name','attackType','attacker.health','attacker.location.x', 'attacker.location.y','attacker.location.z','damageTypeCategory','damage','weapon.itemId','weapon.stackCount','fireWeaponStackCount', # 공격 하나하나 관련된 로그 (당시 공격한 위치는 나오지 않음, 맞은 경우 나옴)
                  'victim.name','damageReason','victimWeapon','victim.health','victim.location.x', 'victim.location.y','victim.location.z','victimWeaponAdditionalInfo','assists_AccountId','victimGameResult.stats.statTrakDataPairs','victimGameResult.stats.headshotStatTrakDataPairs' ,# 피해를 받은 유저
                  'dBNOMaker.name','dBNODamageInfo.damageReason','dBNODamageInfo.damageTypeCategory','dBNODamageInfo.damageCauserName','dBNODamageInfo.additionalInfo','dBNODamageInfo.distance', # 기절을 만든 유저
                  'finisher.name','finisher.health','finishDamageInfo.damageReason','finishDamageInfo.damageTypeCategory','finishDamageInfo.damageCauserName','finishDamageInfo.additionalInfo','finishDamageInfo.distance', # 마무리 유저?
                  'killer.name','killer.health','killerDamageInfo.damageReason','killerDamageInfo.damageTypeCategory','killerDamageInfo.damageCauserName','killerDamageInfo.additionalInfo','killerDamageInfo.distance']] # 킬러 유저?


* ONLY 총으로 인해 받은 damage_log

In [ ]:
from scipy.spatial.distance import euclidean
kill_sample_damage = kill_sample[(kill_sample['_T'].isin(['LogPlayerTakeDamage','LogPlayerAttack'])) & (kill_sample['damageTypeCategory'] == 'Damage_Gun')]

# 각 좌표의 값을 가져오기
attacker_x = kill_sample_damage['attacker.location.x']
attacker_y = kill_sample_damage['attacker.location.y']
attacker_z = kill_sample_damage['attacker.location.z']

victim_x = kill_sample_damage['victim.location.x']
victim_y = kill_sample_damage['victim.location.y']
victim_z = kill_sample_damage['victim.location.z']

# 거리 계산하여 'distance' 열에 추가
kill_sample_damage['distance'] = kill_sample_damage.apply(lambda row: euclidean((row['attacker.location.x'], row['attacker.location.y'], row['attacker.location.z']),
                                                (row['victim.location.x'], row['victim.location.y'], row['victim.location.z'])), axis=1)



kill_sample_damage

<ipython-input-92-c4e851df97c2>:14: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  kill_sample_damage['distance'] = kill_sample_damage.apply(lambda row: euclidean((row['attacker.location.x'], row['attacker.location.y'], row['attacker.location.z']),


_D                   _T character.name  \
4110   2024-05-24T14:10:58.582Z  LogPlayerTakeDamage            NaN   
4150   2024-05-24T14:10:59.874Z  LogPlayerTakeDamage            NaN   
4152   2024-05-24T14:10:59.909Z  LogPlayerTakeDamage            NaN   
4180   2024-05-24T14:11:00.701Z  LogPlayerTakeDamage            NaN   
4184   2024-05-24T14:11:00.782Z  LogPlayerTakeDamage            NaN   
4192   2024-05-24T14:11:00.883Z  LogPlayerTakeDamage            NaN   
4203   2024-05-24T14:11:01.122Z  LogPlayerTakeDamage            NaN   
4224   2024-05-24T14:11:02.264Z  LogPlayerTakeDamage            NaN   
4239   2024-05-24T14:11:02.615Z  LogPlayerTakeDamage            NaN   
4905   2024-05-24T14:11:20.279Z  LogPlayerTakeDamage            NaN   
5218   2024-05-24T14:11:24.746Z  LogPlayerTakeDamage            NaN   
5222   2024-05-24T14:11:24.749Z  LogPlayerTakeDamage            NaN   
5223   2024-05-24T14:11:24.796Z  LogPlayerTakeDamage            NaN   
5241   2024-05-24T14:11:24.903Z  LogPlayerTakeDamage            NaN   
5252   2024-05-24T14:11:24.957Z  LogPlayerTakeDamage            NaN   
5262   2024-05-24T14:11:25.061Z  LogPlayerTakeDamage            NaN   
5266   2024-05-24T14:11:25.067Z  LogPlayerTakeDamage            NaN   
5280   2024-05-24T14:11:25.122Z  LogPlayerTakeDamage            NaN   
5294   2024-05-24T14:11:25.230Z  LogPlayerTakeDamage            NaN   
5296   2024-05-24T14:11:25.235Z  LogPlayerTakeDamage            NaN   
5306   2024-05-24T14:11:25.299Z  LogPlayerTakeDamage            NaN   
5324   2024-05-24T14:11:25.462Z  LogPlayerTakeDamage            NaN   
5332   2024-05-24T14:11:25.471Z  LogPlayerTakeDamage            NaN   
5334   2024-05-24T14:11:25.516Z  LogPlayerTakeDamage            NaN   
5338   2024-05-24T14:11:25.572Z  LogPlayerTakeDamage            NaN   
5356   2024-05-24T14:11:25.687Z  LogPlayerTakeDamage            NaN   
5363   2024-05-24T14:11:25.752Z  LogPlayerTakeDamage            NaN   
5378   2024-05-24T14:11:25.817Z  LogPlayerTakeDamage            NaN   
5383   2024-05-24T14:11:25.920Z  LogPlayerTakeDamage            NaN   
5387   2024-05-24T14:11:26.011Z  LogPlayerTakeDamage            NaN   
5479   2024-05-24T14:11:27.891Z  LogPlayerTakeDamage            NaN   
5488   2024-05-24T14:11:28.046Z  LogPlayerTakeDamage            NaN   
5500   2024-05-24T14:11:28.174Z  LogPlayerTakeDamage            NaN   
5518   2024-05-24T14:11:28.405Z  LogPlayerTakeDamage            NaN   
5574   2024-05-24T14:11:29.058Z  LogPlayerTakeDamage            NaN   
5577   2024-05-24T14:11:29.066Z  LogPlayerTakeDamage            NaN   
5616   2024-05-24T14:11:29.532Z  LogPlayerTakeDamage            NaN   
5651   2024-05-24T14:11:30.001Z  LogPlayerTakeDamage            NaN   
5663   2024-05-24T14:11:30.169Z  LogPlayerTakeDamage            NaN   
5721   2024-05-24T14:11:30.963Z  LogPlayerTakeDamage            NaN   
5735   2024-05-24T14:11:31.142Z  LogPlayerTakeDamage            NaN   
5757   2024-05-24T14:11:31.411Z  LogPlayerTakeDamage            NaN   
5775   2024-05-24T14:11:31.556Z  LogPlayerTakeDamage            NaN   
5778   2024-05-24T14:11:31.603Z  LogPlayerTakeDamage            NaN   
5845   2024-05-24T14:11:32.396Z  LogPlayerTakeDamage            NaN   
5886   2024-05-24T14:11:32.994Z  LogPlayerTakeDamage            NaN   
5939   2024-05-24T14:11:33.564Z  LogPlayerTakeDamage            NaN   
5949   2024-05-24T14:11:33.710Z  LogPlayerTakeDamage            NaN   
5964   2024-05-24T14:11:33.853Z  LogPlayerTakeDamage            NaN   
6003   2024-05-24T14:11:34.332Z  LogPlayerTakeDamage            NaN   
6022   2024-05-24T14:11:34.556Z  LogPlayerTakeDamage            NaN   
6027   2024-05-24T14:11:34.598Z  LogPlayerTakeDamage            NaN   
6046   2024-05-24T14:11:34.836Z  LogPlayerTakeDamage            NaN   
6112   2024-05-24T14:11:35.659Z  LogPlayerTakeDamage            NaN   
6134   2024-05-24T14:11:35.849Z  LogPlayerTakeDamage            NaN   
6170   2024-05-24T14:11:36.361Z  LogPlayerTakeDamage 

In [ ]:
# 'attacker.name', 'victim.name', 'killer.name', 'finisher.name' 컬럼 중 값이 player_name인 경우만 가져오기
cols = (kill_sample['attacker.name'] == player_name) | (kill_sample['victim.name'] == player_name) | (kill_sample['killer.name'] == player_name) | (kill_sample['finisher.name'] == player_name) | (kill_sample['character.name'] == player_name)
player_values = kill_sample[cols]
player_values

_D                   _T    character.name  \
70     2024-05-24T14:08:40.493Z    LogPlayerPosition  VINGMINGVINGMING   
214    2024-05-24T14:08:50.457Z    LogPlayerPosition  VINGMINGVINGMING   
361    2024-05-24T14:09:00.479Z    LogPlayerPosition  VINGMINGVINGMING   
525    2024-05-24T14:09:10.471Z    LogPlayerPosition  VINGMINGVINGMING   
765    2024-05-24T14:09:20.467Z    LogPlayerPosition  VINGMINGVINGMING   
1108   2024-05-24T14:09:30.463Z    LogPlayerPosition  VINGMINGVINGMING   
1830   2024-05-24T14:09:40.494Z    LogPlayerPosition  VINGMINGVINGMING   
2491   2024-05-24T14:09:50.484Z    LogPlayerPosition  VINGMINGVINGMING   
3363   2024-05-24T14:10:00.494Z    LogPlayerPosition  VINGMINGVINGMING   
3464   2024-05-24T14:10:10.485Z    LogPlayerPosition  VINGMINGVINGMING   
3582   2024-05-24T14:10:20.497Z    LogPlayerPosition  VINGMINGVINGMING   
3713   2024-05-24T14:10:30.483Z    LogPlayerPosition  VINGMINGVINGMING   
3835   2024-05-24T14:10:40.477Z    LogPlayerPosition  VINGMINGVINGMING   
3968   2024-05-24T14:10:50.486Z    LogPlayerPosition  VINGMINGVINGMING   
4171   2024-05-24T14:11:00.490Z    LogPlayerPosition  VINGMINGVINGMING   
4483   2024-05-24T14:11:10.492Z    LogPlayerPosition  VINGMINGVINGMING   
4916   2024-05-24T14:11:20.491Z    LogPlayerPosition  VINGMINGVINGMING   
5683   2024-05-24T14:11:30.516Z    LogPlayerPosition  VINGMINGVINGMING   
6485   2024-05-24T14:11:40.484Z    LogPlayerPosition  VINGMINGVINGMING   
7129   2024-05-24T14:11:50.511Z    LogPlayerPosition  VINGMINGVINGMING   
7674   2024-05-24T14:12:00.483Z    LogPlayerPosition  VINGMINGVINGMING   
8227   2024-05-24T14:12:10.507Z    LogPlayerPosition  VINGMINGVINGMING   
8827   2024-05-24T14:12:20.481Z    LogPlayerPosition  VINGMINGVINGMING   
9420   2024-05-24T14:12:30.475Z    LogPlayerPosition  VINGMINGVINGMING   
9977   2024-05-24T14:12:40.483Z    LogPlayerPosition  VINGMINGVINGMING   
10435  2024-05-24T14:12:50.499Z    LogPlayerPosition  VINGMINGVINGMING   
10918  2024-05-24T14:13:00.504Z    LogPlayerPosition  VINGMINGVINGMING   
11385  2024-05-24T14:13:10.486Z    LogPlayerPosition  VINGMINGVINGMING   
11847  2024-05-24T14:13:20.501Z    LogPlayerPosition  VINGMINGVINGMING   
12332  2024-05-24T14:13:30.502Z    LogPlayerPosition  VINGMINGVINGMING   
12848  2024-05-24T14:13:40.475Z    LogPlayerPosition  VINGMINGVINGMING   
13386  2024-05-24T14:13:50.505Z    LogPlayerPosition  VINGMINGVINGMING   
13960  2024-05-24T14:14:00.483Z    LogPlayerPosition  VINGMINGVINGMING   
14343  2024-05-24T14:14:10.494Z    LogPlayerPosition  VINGMINGVINGMING   
14771  2024-05-24T14:14:20.488Z    LogPlayerPosition  VINGMINGVINGMING   
15132  2024-05-24T14:14:30.480Z    LogPlayerPosition  VINGMINGVINGMING   
15566  2024-05-24T14:14:40.484Z    LogPlayerPosition  VINGMINGVINGMING   
15909  2024-05-24T14:14:50.503Z    LogPlayerPosition  VINGMINGVINGMING   
16313  2024-05-24T14:15:00.490Z    LogPlayerPosition  VINGMINGVINGMING   
16680  2024-05-24T14:15:10.479Z    LogPlayerPosition  VINGMINGVINGMING   
17049  2024-05-24T14:15:20.471Z    LogPlayerPosition  VINGMINGVINGMING   
17305  2024-05-24T14:15:30.498Z    LogPlayerPosition  VINGMINGVINGMING   
17653  2024-05-24T14:15:40.502Z    LogPlayerPosition  VINGMINGVINGMING   
17967  2024-05-24T14:15:50.499Z    LogPlayerPosition  VINGMINGVINGMING   
18309  2024-05-24T14:16:00.486Z    LogPlayerPosition  VINGMINGVINGMING   
18583  2024-05-24T14:16:10.476Z    LogPlayerPosition  VINGMINGVINGMING   
18833  2024-05-24T14:16:20.501Z    LogPlayerPosition  VINGMINGVINGMING   
19042  2024-05-24T14:16:30.497Z    LogPlayerPosition  VINGMINGVINGMING   
19262  2024-05-24T14:16:40.485Z    LogPlayerPosition  VINGMINGVINGMING   
19468  2024-05-24T14:16:50.472Z    LogPlayerPosition  VINGMINGVINGMING   
19644  2024-05-24T14:17:00.492Z    LogPlayerPosition  VINGMINGVINGMING   
19728  2024-05-24T14:17:04.158Z      LogPlayerAttack               NaN   
19729  2024-05-24T14:17:04.159Z  LogPlayerTakeDamage               NaN   
19744  2024-05-24T14:17:04.826Z  

* KILL을 확정 낸 경우에만  statTrakDataPairs 로그들이 남는다. 그런데 총관련 밖에 없음.. VALUE 값이 아이템 값인지, 헤드샷 횟수인지 모르겟네

* damageReason 의 경우 피해를 받은 입장에서 로그가 남는다.

In [ ]:
test = kill[['_D','_T','victimGameResult.stats.statTrakDataPairs','victimGameResult.stats.headshotStatTrakDataPairs']]

In [ ]:
from pandas import json_normalize

normalized_data = pd.concat([json_normalize(x) for x in test['victimGameResult.stats.statTrakDataPairs']], ignore_index=True)

In [ ]:
normalized_data

gameItemId  \
0            Item_Skin_SKS_Apocalypse_01_C   
1                 Item_Skin_M762_Dino_01_C   
2                Item_Skin_K2_Unicorn_01_C   
3              Item_Skin_FNFAL_23XMAS_01_C   
4             Item_Skin_Mini14_Pirate_01_C   
5        Item_Skin_M24_Wukong_LV1_01_lv3_C   
6             Item_Skin_HK416_23Bunny_01_C   
7        Item_Skin_FNFAL_Goth_LV2_01_lv9_C   
8  Item_Skin_M762_BlueDragon_LV3_01_lv10_C   

   value  
0     20  
1    116  
2      4  
3      4  
4      6  
5     33  
6     15  
7    227  
8    334


결론, 총기별로 어떤 위치를 얼만큼 맞췄는지 보기 위해서 필요한 컬럼은

TYPE = LogPlayerAttack

* attacker.name
* attackType
* damageReason
* attacker.health
* victim.name


In [3]:
test = player_values[player_values['_T'].isin(['LogPlayerAttack','LogPlayerTakeDamage'])]
test[['attacker.name','attackType','damageReason','attacker.health','victim.name','victim.health']]

NameError: name 'player_values' is not defined

# 첫번째 지표 - 사용성

## 인기도
* TOP30가 장착한 총기비율을 구해주세요
* 어떤 총기가 가장 많이 쓰였는지 확인해주세요
* 유저는 어떤 총을 보면 갈아끼울까요?

In [3]:
# solo log
df = pd.read_csv("/content/drive/MyDrive/PUBG/solo_log_data.csv", encoding = "UTF-8")

# 전체 match_id
file_path = '/content/drive/MyDrive/PUBG/log_details.txt'
f = open(file_path,"r")
data = f.read().split("\n")

# 각 요소를 파싱하여 JSON 객체로 변환하고 큰따옴표를 제거
log_details = []
for item in data:
    item_dict = json.loads(item.replace("'", '"'))
    log_details.append(item_dict)

<ipython-input-3-b61b04732e48>:1: DtypeWarning: Columns (0,4,43,45,46,48,49,50,51,52,55,56,57,64,65,66,67,68,69,70,72,73,74,102,104,105,106,107,109,110,111,112,113,115,116,117,125,126,127,128,129,131,132,134,135,136,153,154,155,156,157,158,159,160,162,163,171,172,173,174,175,176,177,178,179,181,182,190,191,192,193,194,195,196,197,198,200,203,208,211,215,217,222,223,224,232,233,234,235,236,237,238,242,243,244,252,253,254,255,256,257,265,266,267,268,269) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv("/content/drive/MyDrive/PUBG/solo_log_data.csv", encoding = "UTF-8")


In [133]:
# 게임타입 스쿼드가 제일 많음
solo_log = [log for log in log_details if log['game_mode'] == 'solo']
duo_log = [log for log in log_details if log['game_mode'] == 'duo']
squad_log = [log for log in log_details if log['game_mode'] == 'squad']


In [143]:
map_name = [item['map_name'] for item in duo_log]

In [144]:
Counter(map_name)


Counter({'Savage_Main': 248,
         'Chimera_Main': 30,
         'DihorOtok_Main': 28,
         'Neon_Main': 9,
         'Erangel_Main': 19,
         'Baltic_Main': 10,
         'Tiger_Main': 32,
         'Desert_Main': 2})

In [8]:
df = df[df['character.type'] != 'user_ai']


In [82]:
# Savage_Main     29 사녹
# Chimera_Main     7 사녹 파라모
# Erangel_Main     4 에란겔
# Neon_Main        3 헤이
# Tiger_Main       2 에란겔 태이고

df[['mapName']].value_counts()

mapName     
Savage_Main     29
Chimera_Main     7
Erangel_Main     4
Neon_Main        3
Tiger_Main       2
Name: count, dtype: int64

In [4]:
# 유저는 어떤 총을 보면 갈아끼울까?
cols = pd.DataFrame(df.columns)
cols


0
0                                              MatchId
1                                          PingQuality
2                                                   _D
3                                                   _T
4                                            accountId
5                                        common.isGame
6                                       character.name
7                                     character.teamId
8                                     character.health
9                                 character.location.x
10                                character.location.y
11                                character.location.z
12                                   character.ranking
13                         character.individualRanking
14                                 character.accountId
15                              character.isInBlueZone
16                               character.isInRedZone
17                                      character.zone
18                                      character.type
19                                         item.itemId
20                                     item.stackCount
21                                       item.category
22                                    item.subCategory
23                                  item.attachedItems
24                                             vehicle
25                                         elapsedTime
26                                     numAlivePlayers
27                                            attackId
28                                fireWeaponStackCount
29                                          attackType
30                                       attacker.name
31                                     attacker.teamId
32                                     attacker.health
33                                 attacker.location.x
34                                 attacker.location.y
35                                 attacker.location.z
36                                    attacker.ranking
37                          attacker.individualRanking
38                                  attacker.accountId
39                               attacker.isInBlueZone
40                                attacker.isInRedZone
41                                       attacker.zone
42                                       attacker.type
43                                       weapon.itemId
44                                   weapon.stackCount
45                                     weapon.category
46                                  weapon.subCategory
47                                weapon.attachedItems
48                                          objectType
49                                    objectTypeStatus
50                            objectTypeAdditionalInfo
51                                         isLedgeGrab
52                                            weaponId
53                                           fireCount
54                                           seatIndex
55                                    fellowPassengers
56                                 vehicle.vehicleType
57                                   vehicle.vehicleId
58                                   vehicle.seatIndex
59                               vehicle.healthPercent
60                                 vehicle.feulPercent
61                                 vehicle.altitudeAbs
62                                 vehicle.altitudeRel
63                                    vehicle.velocity
64                               vehicle.isWheelsInAir
65                             vehicle.isInWaterVolume
66                                  vehicle.isEngineOn
67                                             mapName
68                                           weatherId
69                                          characters
70                                 cameraViewBehaviour
71                                            teamSize
72                                    

In [9]:
# 아이템을 획득하고 버리는 로그에 남는 컬럼과 필요한 컬럼
# _T, character.name,  item.itemId, item.stackCount, item.category, item.subCategory, GameMode,	MapName,	matchId
# Weapon
item_log = df[df['_T'].isin(['LogItemPickup','LogItemDrop'])]
item_pic_drop = item_log[(item_log['item.category'] == 'Weapon')][[
                                                                    '_D', '_T', 'character.name',
                                                                    'item.itemId', 'item.stackCount', 'item.category',
                                                                     'item.subCategory',	'MapName','matchId']].sort_values(by=['character.name','_D','matchId'])
# item_pic_drop.head(100)


In [10]:
# 무기 장르 list
# hk416 = m4
AR = [
    'Item_Weapon_M16A4_C','Item_Weapon_HK416_C', 'Item_Weapon_AK47_C',
    'Item_Weapon_SCAR-L_C', 'Item_Weapon_G36C_C', 'Item_Weapon_BerylM762_C','Item_Weapon_QBZ95_C', 'Item_Weapon_Mk47Mutant_C',
    'Item_Weapon_AUG_C', 'Item_Weapon_Groza_C','Item_Weapon_ACE32_C','Item_Weapon_FAMASG2_C','Item_Weapon_K2_C']

DMR = [
    'Item_Weapon_Mini14_C', 'Item_Weapon_SKS_C', 'Item_Weapon_Mk14_C', 'Item_Weapon_Mk12_C', 'Item_Weapon_SLR_C',
    'Item_Weapon_QBU88_C', 'Item_Weapon_VSS_C', 'Item_Weapon_Dragunov_C','Item_Weapon_FNFal_C' ]


SMG = [
    'Item_Weapon_UZI_C', 'Item_Weapon_Vector_C', 'Item_Weapon_UMP_C', 'Item_Weapon_TommyGun_C', 'Item_Weapon_Thompson_C','Item_Weapon_Thompson_Old_C',
    'Item_Weapon_PP19Bizon_C','Item_Weapon_MP5K_C', 'Item_Weapon_P90_C','Item_Weapon_JS9_C','Item_Weapon_BizonPP19_C','Item_Weapon_vz61Skorpion_C']

SG = ['Item_Weapon_S686_C', 'Item_Weapon_S1897_C', 'Item_Weapon_S12K_C', 'Item_Weapon_DP12_C', 'Item_Weapon_SawedOff_C',
      'Item_Weapon_Saiga12_C','Item_Weapon_Berreta686_C']


SR = [
    'Item_Weapon_AWM_C', 'Item_Weapon_M24_C', 'Item_Weapon_Kar98k_C', 'Item_Weapon_Win94_C', 'Item_Weapon_MosinNagant_C'
    'Item_Weapon_LynxAMR_C','Item_Weapon_Winchester_C','Item_Weapon_Mosin_C'] # 미라마맵 보급에서만 등장 LynxAMR_C'

Special = ['Item_Weapon_FlareGun_C','Item_Weapon_Mortar_C','Item_Weapon_PanzerFaust100M_C','Item_Weapon_Ziplinegun_C','Item_Weapon_Crossbow_C']

LMG = ['Item_Weapon_M249_C', 'Item_Weapon_DP28_C', 'Item_Weapon_MG3_C']

P = ['Item_Weapon_G18_C', 'Item_Weapon_M1911_C', 'Item_Weapon_M9_C', 'Item_Weapon_Rhino_C',
     'Item_Weapon_NagantM1895_C', 'Item_Weapon_Deagle_C']

Melee = ['Item_Weapon_Pan_C', 'Item_Weapon_Sickle_C', 'Item_Weapon_Machete_C', 'Item_Weapon_Crowbar_C']

Throwables = ['Item_Weapon_Grenade_C', 'Item_Weapon_Molotov_Cocktail_C', 'Item_Weapon_SmokeBomb_C',
              'Item_Weapon_StickyGrenade_C', 'Item_Weapon_StunGrenade_C']



In [11]:
item_pic_drop['weapon.genre'] = [
    'AR' if item in AR else
    'DMR' if item in DMR else
    'SR' if item in SR else
    'SG' if item in SG else
    'SMG' if item in SMG else
    'LMG' if item in LMG else
    'Special' if item in Special else
    'Unknown'
    for item in item_pic_drop['item.itemId']
]


# item_pic_drop.head(100)


matchid, 유저별로

총을 줏은경우 +1 점이 추가가 되고 해당 총을 버린 경우 -1이 되어 0 점이됩니다.
즉, score 1이 많은 경우, 해당 총을 버리지 않고 계속 들고 있다는 뜻 으로 해석할 수 있습니다.

가령, AKM의 SCORE 가 1이 많은 경우, 많은 유저들이 AKM총을 버리지 않고 사용하고 있음을 유추할 수 있습니다. (물론, 파밍문제로 총을 발견하지 못해서 바꾸지 못하는 경우가 있습니다.)


결론적으로 총기별로 score를 다 더하거나 평균을 구해서 해당 총의 인기도를 구했습니다.

In [32]:
# 무기별 점수 계산을 위한 딕셔너리 초기화
user_weapon_scores = {}

# 데이터프레임을 순회하며 각 사용자의 무기별 점수 계산
for index, row in item_pic_drop.iterrows():
    match_id = row['matchId']
    user = row['character.name']
    item = row['item.itemId']
    event_type = row['_T']

    # matchId 및 사용자별 무기별 점수 갱신
    if match_id not in user_weapon_scores:
        user_weapon_scores[match_id] = {}

    if user not in user_weapon_scores[match_id]:
        user_weapon_scores[match_id][user] = {}

    if item not in user_weapon_scores[match_id][user]:
        user_weapon_scores[match_id][user][item] = 0

    if event_type == 'LogItemPickup':
        user_weapon_scores[match_id][user][item] += 1
    elif event_type == 'LogItemDrop':
        user_weapon_scores[match_id][user][item] -= 1




In [33]:
# 데이터프레임으로 변환
df_list = []
for match_id, user_scores in user_weapon_scores.items():
    for user, weapon_scores in user_scores.items():
        for weapon, score in weapon_scores.items():
            df_list.append({'matchId': match_id, 'character.name': user, 'item.itemId': weapon, 'weapon_score': score})

result_df = pd.DataFrame(df_list)



In [52]:
item_score = result_df.groupby(['item.itemId']).agg(
    score_mean = pd.NamedAgg(column='weapon_score',aggfunc='mean'),
    score_sum = pd.NamedAgg(column='weapon_score',aggfunc='sum')
    ).reset_index().sort_values(by=['score_mean','weapon.genre'],ascending=False)

item_score['weapon.genre'] = [
    'AR' if item in AR else
    'DMR' if item in DMR else
    'SR' if item in SR else
    'SG' if item in SG else
    'SMG' if item in SMG else
    'LMG' if item in LMG else
    'Special' if item in Special else
    'Unknown'
    for item in item_score['item.itemId']
]

item_score[item_score['weapon.genre']== 'AR']

item.itemId  score_mean  score_sum weapon.genre
17       Item_Weapon_Groza_C    0.941176         16           AR
13     Item_Weapon_FAMASG2_C    0.875000         14           AR
5    Item_Weapon_BerylM762_C    0.729776        424           AR
2          Item_Weapon_AUG_C    0.670259        311           AR
18       Item_Weapon_HK416_C    0.660377        420           AR
0        Item_Weapon_ACE32_C    0.646715        443           AR
20          Item_Weapon_K2_C    0.555556          5           AR
42       Item_Weapon_QBZ95_C    0.498965        241           AR
44      Item_Weapon_SCAR-L_C    0.488372         21           AR
33  Item_Weapon_Mk47Mutant_C    0.422819         63           AR
1         Item_Weapon_AK47_C    0.410638        193           AR
22       Item_Weapon_M16A4_C    0.321586         73           AR

* Score_sum과 mean 높은 경우 = 해당 총을 줍고 버리지 않은 경우
* Score_sum은 높지만 mean은 낮은 경우 = 해당 총을 줍고 버리는 경우가 많은 경우
* Score_sum은 낮지만 score_mean이 높은 경우 = SS급 1티어 총기(보급에서만 나오는) 경우일 수 있습니다.


AR의 경우


In [69]:
gun = item_score[item_score['weapon.genre'].isin(['DMR','AR','SMR','SR'])].sort_values(by=['weapon.genre','score_mean'],ascending=False)

In [76]:
groupby_item = item_pic_drop.groupby(['_T','item.itemId','weapon.genre']).agg(
    pickup_count=('item.itemId', 'count')).reset_index().sort_values(by=['_T','weapon.genre','pickup_count'],ascending=False)
pickup = groupby_item[groupby_item['_T']=='LogItemPickup'][['item.itemId','pickup_count']]
merged_df = pd.merge(gun, pickup,on='item.itemId', how='left')


In [79]:
drop = groupby_item[groupby_item['_T']=='LogItemDrop'][['item.itemId','pickup_count']]
drop

item.itemId  pickup_count
37              Item_Weapon_Pan_C            50
26              Item_Weapon_M79_C            30
29          Item_Weapon_Machete_C            22
47           Item_Weapon_Sickle_C            14
7            Item_Weapon_Cowbar_C            13
23            Item_Weapon_M1911_C            13
16              Item_Weapon_G18_C            12
46          Item_Weapon_Sawnoff_C            12
35      Item_Weapon_NagantM1895_C            11
27               Item_Weapon_M9_C             8
11      Item_Weapon_DesertEagle_C             4
39          Item_Weapon_Pickaxe_C             2
42            Item_Weapon_Rhino_C             2
48          Item_Weapon_StunGun_C             2
38  Item_Weapon_PanzerFaust100M_C            20
15         Item_Weapon_FlareGun_C            18
8          Item_Weapon_Crossbow_C            12
33           Item_Weapon_Mortar_C             6
55       Item_Weapon_Ziplinegun_C             4
21           Item_Weapon_Kar98k_C           172
25              Item_Weapon_M24_C           109
54       Item_Weapon_Winchester_C            52
34            Item_Weapon_Mosin_C            11
3               Item_Weapon_AWM_C             4
53           Item_Weapon_Vector_C           262
50              Item_Weapon_UMP_C           167
51              Item_Weapon_UZI_C           150
49         Item_Weapon_Thompson_C            90
56     Item_Weapon_vz61Skorpion_C            13
19              Item_Weapon_JS9_C            11
6         Item_Weapon_BizonPP19_C             4
36              Item_Weapon_P90_C             4
45          Item_Weapon_Saiga12_C           130
4        Item_Weapon_Berreta686_C            75
9              Item_Weapon_DP12_C            57
24             Item_Weapon_M249_C            75
10             Item_Weapon_DP28_C             8
28              Item_Weapon_MG3_C             3
40            Item_Weapon_QBU88_C           201
44              Item_Weapon_SKS_C           184
12         Item_Weapon_Dragunov_C           125
14            Item_Weapon_FNFal_C           113
31             Item_Weapon_Mk12_C            94
52              Item_Weapon_VSS_C            60
30           Item_Weapon_Mini14_C            35
1              Item_Weapon_AK47_C           328
0             Item_Weapon_ACE32_C           298
41            Item_Weapon_QBZ95_C           276
18            Item_Weapon_HK416_C           269
5         Item_Weapon_BerylM762_C           215
2               Item_Weapon_AUG_C           199
22            Item_Weapon_M16A4_C           166
32       Item_Weapon_Mk47Mutant_C            97
43           Item_Weapon_SCAR-L_C            25
20               Item_Weapon_K2_C             5
13          Item_Weapon_FAMASG2_C             4
17            Item_Weapon_Groza_C             3

In [80]:
merged_df[merged_df['weapon.genre'] == 'AR'].sort_values(by=['weapon.genre','score_mean'],ascending=False)

item.itemId  score_mean  score_sum weapon.genre  pickup_count
13       Item_Weapon_Groza_C    0.941176         16           AR            19
14     Item_Weapon_FAMASG2_C    0.875000         14           AR            18
15   Item_Weapon_BerylM762_C    0.729776        424           AR           639
16         Item_Weapon_AUG_C    0.670259        311           AR           510
17       Item_Weapon_HK416_C    0.660377        420           AR           689
18       Item_Weapon_ACE32_C    0.646715        443           AR           741
19          Item_Weapon_K2_C    0.555556          5           AR            10
20       Item_Weapon_QBZ95_C    0.498965        241           AR           517
21      Item_Weapon_SCAR-L_C    0.488372         21           AR            46
22  Item_Weapon_Mk47Mutant_C    0.422819         63           AR           160
23        Item_Weapon_AK47_C    0.410638        193           AR           521
24       Item_Weapon_M16A4_C    0.321586         73           AR           239



 500번 이상 pickup 로그가 발생된 총기만 보았을 때,
* AR의 경우 베릴, M4(HK4), 어그, 에이스, AK47(AKM) 가 대부분을 차지하고 있습니다.
* 하지만 유저가 **해당총을 습득하고 다른 총으로 갈아탄 지표**에 해당하는 `score_mean` 을 보면  AK47의 경우 0.41로 가장 저조합니다.

* 1-0.41 = 59% 유저가 다른총으로 갈아탄다고 볼 수 있습니다.

* 베릴의 경우 유저가 가장 많이 선택하고, 갈아타지 않는 총입니다.

(Groza, famas 같은 보급형의 경우 제외)


> 패치이전 AKM의 인기도가 어느정도인지 정확히는 알수 없지만 여전히 유저들이 PickUp 하고 있는 총기임에는 분명합니다. 하지만 다른총이 나왔을 때 갈아타는 수치가 꽤 높은 편입니다.

한계점) 맵의 편차가 있기 때문에 한계가 있음. 특정 맵에만 나오는 총이 있기 때문에, 해당 데이터의 경우 맵이 사녹인 경기가 많다..`
